In [1]:
import pandas as pd 
import keras
from keras.utils import np_utils
from keras.models import Sequential
from keras.layers import Dense, Activation
from keras.optimizers import SGD
import matplotlib.pyplot as plt

2023-06-07 08:02:58.122780: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2023-06-07 08:03:07.100254: I tensorflow/tsl/cuda/cudart_stub.cc:28] Could not find cuda drivers on your machine, GPU will not be used.
2023-06-07 08:03:07.147382: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-06-07 08:03:22.249443: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


In [2]:
dados ='/home/dev/PycharmProjects/FallDetection/dados.npy'
rotulos ='/home/dev/PycharmProjects/FallDetection/rotulos.npy'

In [3]:
import numpy as np
X = np.load(dados)
y = np.load(rotulos)

In [4]:
from sklearn.model_selection import train_test_split

# Dividindo os dados em conjunto de treinamento e teste
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Dividindo o conjunto de treinamento em conjunto de treinamento e validação
X_train, X_val, y_train, y_val = train_test_split(X_train, y_train, test_size=0.2, random_state=42)

In [5]:
X_train.shape

(988, 400, 1)

In [6]:
X_train.tolist()
y_train.tolist()
X_test.tolist()
y_test.tolist()
X_val.tolist()
y_val.tolist()


[1,
 6,
 5,
 6,
 2,
 6,
 4,
 0,
 3,
 5,
 4,
 5,
 5,
 0,
 4,
 7,
 0,
 4,
 6,
 2,
 4,
 2,
 6,
 1,
 6,
 6,
 7,
 2,
 4,
 0,
 6,
 4,
 2,
 0,
 6,
 6,
 0,
 4,
 4,
 2,
 3,
 3,
 0,
 2,
 6,
 0,
 4,
 5,
 4,
 6,
 2,
 0,
 6,
 4,
 0,
 6,
 1,
 0,
 2,
 0,
 6,
 0,
 7,
 0,
 6,
 1,
 5,
 1,
 4,
 1,
 4,
 5,
 3,
 0,
 1,
 4,
 0,
 6,
 4,
 0,
 4,
 1,
 4,
 1,
 2,
 4,
 2,
 2,
 0,
 4,
 5,
 4,
 0,
 0,
 1,
 7,
 5,
 7,
 1,
 6,
 2,
 4,
 6,
 6,
 3,
 4,
 6,
 5,
 3,
 5,
 5,
 4,
 2,
 0,
 5,
 4,
 1,
 0,
 1,
 4,
 0,
 1,
 2,
 4,
 3,
 6,
 0,
 6,
 6,
 0,
 6,
 0,
 6,
 6,
 5,
 6,
 2,
 6,
 6,
 2,
 0,
 4,
 2,
 4,
 1,
 4,
 5,
 5,
 1,
 2,
 2,
 2,
 2,
 2,
 0,
 1,
 0,
 4,
 6,
 1,
 2,
 6,
 1,
 4,
 0,
 4,
 2,
 4,
 3,
 6,
 4,
 0,
 6,
 1,
 7,
 6,
 1,
 4,
 4,
 2,
 1,
 0,
 6,
 1,
 0,
 2,
 6,
 0,
 0,
 6,
 4,
 4,
 6,
 5,
 4,
 3,
 0,
 5,
 6,
 1,
 4,
 1,
 5,
 6,
 1,
 5,
 1,
 0,
 1,
 6,
 6,
 5,
 3,
 6,
 0,
 4,
 1,
 2,
 4,
 0,
 1,
 4,
 7,
 4,
 6,
 4,
 2,
 1,
 6,
 2,
 4,
 4,
 1,
 6,
 1,
 4,
 2,
 5,
 1,
 4,
 2,
 6,
 0,
 1,
 2,
 5,
 2]

In [7]:
batch = int(len(y_train)/30)
batch

32

In [8]:
from keras.utils import np_utils
y_train_convertido = np_utils.to_categorical(y_train)
y_test_convertido =  np_utils.to_categorical(y_test)
y_val_convertido =  np_utils.to_categorical(y_val)

In [9]:
from keras.models import Sequential
from keras.layers import Dense, Activation,Dropout

In [10]:
import optuna
from keras.optimizers import SGD

def objective(trial):
    
    # Definindo o espaço de busca dos hiperparâmetros
    
    num_layers = trial.suggest_int('num_layers', 2, 7)
    dense_neurons = trial.suggest_int('dense_neurons', 20, 4000, log=True)
    dropout = trial.suggest_int('dropout', 2, 5, step=1) / 10.0
    
    modelo = Sequential()
    
    for i in range(num_layers):
        if i == 0:
            modelo.add(Dense(dense_neurons, input_dim=400, kernel_initializer='normal',activation='relu'))
            modelo.add(Dropout(dropout))
        else:
            modelo.add(Dense(dense_neurons, kernel_initializer='normal',activation='relu'))
            modelo.add(Dropout(dropout))

    modelo.add(Dense(8, kernel_initializer='normal',activation = 'softmax'))
                     
    otimizador = SGD() 
    modelo.compile(loss="categorical_crossentropy",optimizer=otimizador,metrics =["acc"])
    historico = modelo.fit(X_train,y_train_convertido, epochs= 500, batch_size = batch, validation_data=(X_val,y_val_convertido),verbose = 1)
    
    return historico.history['val_acc'][-1]

In [ ]:
import csv

# criação do objeto de estudo
study = optuna.create_study(direction="maximize")

# abertura do arquivo CSV em modo de escrita
with open("results.csv", "w", newline="") as csvfile:
    writer = csv.writer(csvfile, delimiter=",")
    writer.writerow(["trial", "accuracy", "hyperparameters"])  # cabeçalho

    # iteração dos trials
    
    study.optimize(objective, n_trials=180)
    best_trial = study.best_trial
    i = study.trials[0].number  # Obtém o número do primeiro trial realizado
    print("Trial {}: Accuracy = {}".format(i, best_trial.value))

    # escrita dos valores no arquivo CSV
    writer.writerow([i, best_trial.value, best_trial.params])

    print("Trial {}: Accuracy = {}".format(i, best_trial.value))


print(study.best_params)



[I 2023-06-07 08:03:52,256] A new study created in memory with name: no-name-1dfc41c1-a7a6-493a-a2ab-6e77f26ff306
2023-06-07 08:03:54.025600: I tensorflow/compiler/xla/stream_executor/cuda/cuda_gpu_executor.cc:996] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355
2023-06-07 08:03:54.026484: W tensorflow/core/common_runtime/gpu/gpu_device.cc:1956] Cannot dlopen some GPU libraries. Please make sure the missing libraries mentioned above are installed properly if you would like to use GPU. Follow the guide at https://www.tensorflow.org/install/gpu for how to download and setup the required libraries for your platform.
Skipping registering GPU devices...


Epoch 1/500
31/31 [==============================] - 3s 9ms/step - loss: 2.0741 - acc: 0.1862 - val_loss: 2.0696 - val_acc: 0.2267
Epoch 2/500
31/31 [==============================] - 0s 2ms/step - loss: 2.0631 - acc: 0.1933 - val_loss: 2.0609 - val_acc: 0.1619
Epoch 3/500
31/31 [==============================] - 0s 2ms/step - loss: 2.0537 - acc: 0.2095 - val_loss: 2.0528 - val_acc: 0.1538
Epoch 4/500
31/31 [==============================] - 0s 2ms/step - loss: 2.0444 - acc: 0.1974 - val_loss: 2.0454 - val_acc: 0.2308
Epoch 5/500
31/31 [==============================] - 0s 2ms/step - loss: 2.0362 - acc: 0.1933 - val_loss: 2.0386 - val_acc: 0.2146
Epoch 6/500
31/31 [==============================] - 0s 2ms/step - loss: 2.0282 - acc: 0.2055 - val_loss: 2.0324 - val_acc: 0.1862
Epoch 7/500
31/31 [==============================] - 0s 2ms/step - loss: 2.0211 - acc: 0.2065 - val_loss: 2.0266 - val_acc: 0.2024
Epoch 8/500
31/31 [==============================] - 0s 2ms/step - loss: 2.0145 - a

[I 2023-06-07 08:04:34,928] Trial 0 finished with value: 0.6032388806343079 and parameters: {'num_layers': 5, 'dense_neurons': 81, 'dropout': 4}. Best is trial 0 with value: 0.6032388806343079.


Epoch 1/500
31/31 [==============================] - 0s 5ms/step - loss: 2.0624 - acc: 0.1559 - val_loss: 2.0426 - val_acc: 0.1781
Epoch 2/500
31/31 [==============================] - 0s 2ms/step - loss: 2.0313 - acc: 0.1842 - val_loss: 2.0176 - val_acc: 0.1741
Epoch 3/500
31/31 [==============================] - 0s 2ms/step - loss: 2.0032 - acc: 0.2095 - val_loss: 1.9937 - val_acc: 0.1943
Epoch 4/500
31/31 [==============================] - 0s 2ms/step - loss: 1.9876 - acc: 0.1974 - val_loss: 1.9755 - val_acc: 0.1943
Epoch 5/500
31/31 [==============================] - 0s 2ms/step - loss: 1.9673 - acc: 0.2004 - val_loss: 1.9640 - val_acc: 0.1943
Epoch 6/500
31/31 [==============================] - 0s 2ms/step - loss: 1.9610 - acc: 0.1903 - val_loss: 1.9571 - val_acc: 0.1943
Epoch 7/500
31/31 [==============================] - 0s 2ms/step - loss: 1.9568 - acc: 0.2024 - val_loss: 1.9520 - val_acc: 0.2065
Epoch 8/500
31/31 [==============================] - 0s 2ms/step - loss: 1.9534 - a

[I 2023-06-07 08:05:08,087] Trial 1 finished with value: 0.8502024412155151 and parameters: {'num_layers': 3, 'dense_neurons': 96, 'dropout': 5}. Best is trial 1 with value: 0.8502024412155151.


...

Epoch 1/500
31/31 [==============================] - 2s 56ms/step - loss: 18.7270 - acc: 0.1872 - val_loss: 3.0836 - val_acc: 0.2267
Epoch 2/500
31/31 [==============================] - 2s 52ms/step - loss: 3.2567 - acc: 0.2540 - val_loss: 1.5872 - val_acc: 0.5061
Epoch 3/500
31/31 [==============================] - 2s 51ms/step - loss: 2.1844 - acc: 0.2692 - val_loss: 1.4729 - val_acc: 0.5385
Epoch 4/500
31/31 [==============================] - 2s 52ms/step - loss: 1.8886 - acc: 0.3128 - val_loss: 1.3843 - val_acc: 0.6356
Epoch 5/500
31/31 [==============================] - 2s 52ms/step - loss: 1.7439 - acc: 0.3816 - val_loss: 1.3238 - val_acc: 0.6518
Epoch 6/500
31/31 [==============================] - 2s 51ms/step - loss: 1.7130 - acc: 0.3745 - val_loss: 1.3489 - val_acc: 0.3968
Epoch 7/500
31/31 [==============================] - 2s 51ms/step - loss: 1.6599 - acc: 0.3877 - val_loss: 1.2557 - val_acc: 0.6235
Epoch 8/500
31/31 [==============================] - 2s 52ms/step - loss: 1

[I 2023-06-07 16:08:18,006] Trial 87 finished with value: 0.8137651681900024 and parameters: {'num_layers': 3, 'dense_neurons': 2624, 'dropout': 5}. Best is trial 52 with value: 0.8866396546363831.


Epoch 1/500
31/31 [==============================] - 1s 20ms/step - loss: 5.8500 - acc: 0.2024 - val_loss: 1.8879 - val_acc: 0.3117
Epoch 2/500
31/31 [==============================] - 1s 17ms/step - loss: 2.1389 - acc: 0.3715 - val_loss: 1.2378 - val_acc: 0.6073
Epoch 3/500
31/31 [==============================] - 1s 17ms/step - loss: 1.6443 - acc: 0.4636 - val_loss: 1.2438 - val_acc: 0.5223
Epoch 4/500
31/31 [==============================] - 1s 17ms/step - loss: 1.3396 - acc: 0.5354 - val_loss: 1.0406 - val_acc: 0.6437
Epoch 5/500
31/31 [==============================] - 1s 17ms/step - loss: 1.2971 - acc: 0.5587 - val_loss: 1.0090 - val_acc: 0.6802
Epoch 6/500
31/31 [==============================] - 1s 17ms/step - loss: 1.1031 - acc: 0.6366 - val_loss: 0.8933 - val_acc: 0.7045
Epoch 7/500
31/31 [==============================] - 1s 17ms/step - loss: 1.0974 - acc: 0.6397 - val_loss: 0.8928 - val_acc: 0.6721
Epoch 8/500
31/31 [==============================] - 1s 17ms/step - loss: 1.

[I 2023-06-07 16:13:12,807] Trial 88 finished with value: 0.8663967847824097 and parameters: {'num_layers': 2, 'dense_neurons': 1984, 'dropout': 5}. Best is trial 52 with value: 0.8866396546363831.


Epoch 1/500
31/31 [==============================] - 2s 62ms/step - loss: 15.8990 - acc: 0.2389 - val_loss: 4.2149 - val_acc: 0.2996
Epoch 2/500
31/31 [==============================] - 2s 59ms/step - loss: 2.3701 - acc: 0.4099 - val_loss: 1.3988 - val_acc: 0.5263
Epoch 3/500
31/31 [==============================] - 2s 59ms/step - loss: 1.6698 - acc: 0.4889 - val_loss: 0.9318 - val_acc: 0.7287
Epoch 4/500
31/31 [==============================] - 2s 58ms/step - loss: 1.3748 - acc: 0.5638 - val_loss: 1.0114 - val_acc: 0.6356
Epoch 5/500
31/31 [==============================] - 2s 60ms/step - loss: 1.2336 - acc: 0.5860 - val_loss: 0.9469 - val_acc: 0.6923
Epoch 6/500
31/31 [==============================] - 2s 58ms/step - loss: 1.0919 - acc: 0.6407 - val_loss: 0.9209 - val_acc: 0.7085
Epoch 7/500
31/31 [==============================] - 2s 61ms/step - loss: 1.0315 - acc: 0.6437 - val_loss: 0.7755 - val_acc: 0.7409
Epoch 8/500
31/31 [==============================] - 2s 58ms/step - loss: 0